In [30]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.signal import find_peaks
import glob
import warnings
import pickle
warnings.filterwarnings('ignore')

In [44]:
def load_and_find_spikes(path):
    print(path)
    if "PNs" in path:
        label = "PN"
    else:
        label = "LN"

    cur_df = pd.read_csv(path, sep='     ',header=None,skiprows=12,usecols=[1,2])
    #print(path[-13:-4])
    
    #find spikes with find_peak
    timestamp_indices, _ = find_peaks(cur_df.iloc[:,1],\
                                      height = cur_df.iloc[:,1].max()/3)
    #print(timestamp_indices)
    timestamps = np.array(cur_df.iloc[timestamp_indices,0])
    cor_values = np.array(cur_df.iloc[timestamp_indices,1])

    org_timestamps = np.array(cur_df.iloc[:,0])
    org_cor_values = np.array(cur_df.iloc[:,1])


    print(timestamp_indices)

    #print(path[-13:-4],label,timestamps)
    #save dataframe with columns mothname, label, timestamps
    return  pd.DataFrame([[path[-13:-4],label,timestamps,cor_values,org_timestamps,org_cor_values,timestamp_indices]],\
                         columns=['mothname','label','timestamps','cor_values',\
                                'org_timestamps','org_cor_values','timestamp_indices'])

vec_load_and_find_spikes = np.vectorize(load_and_find_spikes)

def load_all(directory_name):
    #use glob.glob to recheive all txt files in label_data folder, which is in the parent directory of the parent directory
    #of this file

    label_data = np.array(glob.glob(f"{directory_name}/**/*.txt",recursive=True))

    vec_np_result = vec_load_and_find_spikes(label_data)

    #for each row of vec_np_result, add it as a row to res dataframe
    res = pd.concat(vec_np_result,axis = 0,ignore_index=True)
    return res



spike_df = load_all("/Users/Ocelottamer/Documents/GitHub/AL_generative/labeled_data")
#pickle the dataframe (which essentially stores the timestamps data)
spike_df.to_pickle("spike_df.pkl")

    

/Users/Ocelottamer/Documents/GitHub/AL_generative/labeled_data/**/*.txt
/Users/Ocelottamer/Documents/GitHub/AL_generative/labeled_data/LNs/CR060324A/060324124.txt
[ 2132  9082 12028 18901 23650 27802 34639 39143 40962 43908 47234 50371
 52320 52322 55351 56830 60995 66987 72033 74240 82385 89290 98021 99828]
/Users/Ocelottamer/Documents/GitHub/AL_generative/labeled_data/LNs/CR060324A/060324124.txt
[ 2132  9082 12028 18901 23650 27802 34639 39143 40962 43908 47234 50371
 52320 52322 55351 56830 60995 66987 72033 74240 82385 89290 98021 99828]
/Users/Ocelottamer/Documents/GitHub/AL_generative/labeled_data/LNs/CR071031A/071031002.txt
[   405    828   1334   1727   2068   2549   2806   3247   3710   4263
   4832   5240   6187   6808   7263   7991   8505   9004   9444   9910
  10412  11011  11487  12122  12508  12778  13585  14010  14649  15320
  15945  16401  16914  17315  17730  18170  19025  19587  20702  20705
  21710  22430  22432  22784  23090  23381  23766  23768  24059  24360
  2467

In [45]:
with open('spike_df.pkl', 'rb') as f:
    spike_df = pickle.load(f)

#plot the spike timestamps and corresponding cor values, use subplots to store each row of spike_df
#in a separate subplot
fig, axs = plt.subplots(len(spike_df),figsize=(30,300))
for i in range(len(spike_df)):
    axs[i].scatter(spike_df.iloc[i,2],spike_df.iloc[i,3],color = 'red')
    axs[i].plot(spike_df.iloc[i,4],spike_df.iloc[i,5],color = 'blue')
    axs[i].set_title(spike_df.iloc[i,0] + " " + spike_df.iloc[i,1])
    axs[i].set_xlabel("timestamps")
    axs[i].set_ylabel("cor values")
#save figure 
plt.savefig("spike_timestamps.jpg")

plt.show()